# ETL Project
### ***NFL Draft Analysis***

In [1]:
#Import Dependencies
import pandas as pd
from sqlalchemy import create_engine
import psycopg2
import sqlalchemy
from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session
from sqlalchemy import create_engine, func, inspect

# Extract

##### Extract the data from Wikipedia and  www.pro-football-reference.com. 
* Note: Since we are scraping data from tables we are using pandas otherwise we were going to need to use BeatifulSoup and Splinter

### Extract Draft Info from 2016-2020

In [2]:
years = (2016,2017,2018,2019,2020)
draft = pd.DataFrame()
for year in years:
    url = f'https://www.pro-football-reference.com/years/{year}/draft.htm'
    print(url)
    print('----------')
    read = pd.read_html(url)
    table = read[0]
    table.columns = table.columns.droplevel()
    table['year'] = year
    draft = draft.append(table, ignore_index=True)
draft

https://www.pro-football-reference.com/years/2016/draft.htm
----------
https://www.pro-football-reference.com/years/2017/draft.htm
----------
https://www.pro-football-reference.com/years/2018/draft.htm
----------
https://www.pro-football-reference.com/years/2019/draft.htm
----------
https://www.pro-football-reference.com/years/2020/draft.htm
----------


Rnd Pick   Tm            Player Pos Age    To AP1 PB St  ...   TD  Rec  \
0      1    1  LAR        Jared Goff  QB  21  2021   0  2  5  ...   10    0   
1      1    2  PHI      Carson Wentz  QB  23  2021   0  1  6  ...    9    2   
2      1    3  SDG         Joey Bosa  DE  21  2021   0  3  6  ...    0    0   
3      1    4  DAL   Ezekiel Elliott  RB  21  2021   1  3  6  ...   54  282   
4      1    5  JAX      Jalen Ramsey  CB  21  2021   2  4  6  ...    0    0   
...   ..  ...  ...               ...  ..  ..   ...  .. .. ..  ...  ...  ...   
1296   7  251  SEA  Stephen Sullivan  TE  23  2020   0  0  0  ...    0    0   
1297   7  252  DEN   Tyrie Cleveland  WR  22  2021   0  0  0  ...    0    6   
1298   7  253  MIN       Kyle Hinton   G  22   NaN   0  0  0  ...  NaN  NaN   
1299   7  254  DEN     Derrek Tuszka  LB  24  2021   0  0  0  ...    0    0   
1300   7  255  NYG       Tae Crowder  LB  23  2021   0  0  2  ...    0    0   

       Yds   TD Solo  Int    Sk      College/Univ Unnamed: 28_level_1  year  
0        0    0  NaN  NaN   NaN        California       College Stats  2016  
1       11    0  NaN  NaN   NaN  North Dakota St.       College Stats  2016  
2        0    0  205  NaN  56.0          Ohio St.       College Stats  2016  
3     2202   11    1  NaN   NaN          Ohio St.       College Stats  2016  
4        0    0  295   14   NaN       Florida St.       College Stats  2016  
...    ...  ...  ...  ...   ...               ...                 ...   ...  
1296     0    0  NaN  NaN   NaN               LSU       College Stats  2020  
1297    63    0    4  NaN   NaN           Florida       College Stats  2020  
1298   NaN  NaN  NaN  NaN   NaN          Washburn                 NaN  2020  
1299     0    0    9  NaN   NaN  North Dakota St.                 NaN  2020  
1300     0    0   83    1   1.0           Georgia       College Stats  2020  

[1301 rows x 30 columns]

# Transform

In [3]:
# Select the columns we are going to use
df = draft[['Rnd','Pick','Player','Pos','Age','College/Univ', 'year']]
df

Rnd Pick            Player Pos Age      College/Univ  year
0      1    1        Jared Goff  QB  21        California  2016
1      1    2      Carson Wentz  QB  23  North Dakota St.  2016
2      1    3         Joey Bosa  DE  21          Ohio St.  2016
3      1    4   Ezekiel Elliott  RB  21          Ohio St.  2016
4      1    5      Jalen Ramsey  CB  21       Florida St.  2016
...   ..  ...               ...  ..  ..               ...   ...
1296   7  251  Stephen Sullivan  TE  23               LSU  2020
1297   7  252   Tyrie Cleveland  WR  22           Florida  2020
1298   7  253       Kyle Hinton   G  22          Washburn  2020
1299   7  254     Derrek Tuszka  LB  24  North Dakota St.  2020
1300   7  255       Tae Crowder  LB  23           Georgia  2020

[1301 rows x 7 columns]

In [4]:
# Save to csv to get the index to use it as ID
df.to_csv('../resources/nfl_draft2016-2020', header=True)

In [42]:
# read the csv to get first column and use it as id
draft = pd.read_csv('../resources/nfl_draft2016-2020')
draft

Unnamed: 0  Rnd  Pick                    Player  Pos  Age  \
0              0    1     1                Jared Goff   QB   21   
1              1    1     2              Carson Wentz   QB   23   
2              2    1     3                 Joey Bosa   DE   21   
3              3    1     4           Ezekiel Elliott   RB   21   
4              4    1     5              Jalen Ramsey   CB   21   
5              5    1     6            Ronnie Stanley    T   22   
6              6    1     7          DeForest Buckner   DE   22   
7              7    1     8              Jack Conklin    T   22   
8              8    1     9             Leonard Floyd  OLB   23   
9              9    1    10                 Eli Apple   CB   21   
10            10    1    11     Vernon Hargreaves III   CB   21   
11            11    1    12           Sheldon Rankins   DT   22   
12            12    1    13             Laremy Tunsil    T   22   
13            13    1    14               Karl Joseph    S   22   
14            14    1    15             Corey Coleman   WR   22   
15            15    1    16             Taylor Decker    T   23   
16            16    1    17                Keanu Neal    S   21   
17            17    1    18                Ryan Kelly    C   23   
18            18    1    19               Shaq Lawson   DE   22   
19            19    1    20                Darron Lee  OLB   21   
20            20    1    21               Will Fuller   WR   22   
21            21    1    22              Josh Doctson   WR   23   
22            22    1    23          Laquon Treadwell   WR   21   
23            23    1    24       William Jackson III   CB   23   
24            24    1    25               Artie Burns   CB   21   
25            25    1    26              Paxton Lynch   QB   22   
26            26    1    27               Kenny Clark   DT   20   
27            27    1    28            Joshua Garnett    G   22   
28            28    1    29          Robert Nkemdiche   DT   21   
29            29    1    30             Vernon Butler   DT   22   
30            30    1    31             Germain Ifedi    G   22   
31            31  Rnd  Pick                    Player  Pos  Age   
32            32    2    32            Emmanuel Ogbah   DE   22   
33            33    2    33                Kevin Dodd   DE   24   
34            34    2    34              Jaylon Smith  OLB   21   
35            35    2    35              Hunter Henry   TE   21   
36            36    2    36                Myles Jack  OLB   21   
37            37    2    37               Chris Jones   DT   22   
38            38    2    38             Xavien Howard   CB   23   
39            39    2    39               Noah Spence   DE   22   
40            40    2    40          Sterling Shepard   WR   23   
41            41    2    41            Reggie Ragland  ILB   22   
42            42    2    42            Kamalei Correa   DE   22   
43            43    2    43            Austin Johnson   NT   22   
44            44    2    44                Jihad Ward   DE   22   
45            45    2    45             Derrick Henry   RB   22   
46            46    2    46          A'Shawn Robinson   DT   21   
47            47    2    47            Michael Thomas   WR   23   
48            48    2    48             Jason Spriggs    T   22   
49            49    2    49               Jarran Reed   DT   23   
50            50    2    50               Nick Martin    G   23   
51            51    2    51      Christian Hackenberg   QB   21   
52            52    2    52               Deion Jones  OLB   21   
53            53    2    53              Su'a Cravens  OLB   21   
54            54    2    54       Mackensie Alexander   CB   22   
55            55    2    55                Tyler Boyd   WR   21   
56            56    2    56            Cody Whitehair    G   24   
57            57    2    57                T.J. Green    S   21   
58            58    2    58                Sean Davis

In [43]:
# rename first column as player_id
draft = draft.rename(columns={'Unnamed: 0':'player_id','College/Univ': 'college'})
draft

player_id  Rnd  Pick                    Player  Pos  Age  \
0             0    1     1                Jared Goff   QB   21   
1             1    1     2              Carson Wentz   QB   23   
2             2    1     3                 Joey Bosa   DE   21   
3             3    1     4           Ezekiel Elliott   RB   21   
4             4    1     5              Jalen Ramsey   CB   21   
5             5    1     6            Ronnie Stanley    T   22   
6             6    1     7          DeForest Buckner   DE   22   
7             7    1     8              Jack Conklin    T   22   
8             8    1     9             Leonard Floyd  OLB   23   
9             9    1    10                 Eli Apple   CB   21   
10           10    1    11     Vernon Hargreaves III   CB   21   
11           11    1    12           Sheldon Rankins   DT   22   
12           12    1    13             Laremy Tunsil    T   22   
13           13    1    14               Karl Joseph    S   22   
14           14    1    15             Corey Coleman   WR   22   
15           15    1    16             Taylor Decker    T   23   
16           16    1    17                Keanu Neal    S   21   
17           17    1    18                Ryan Kelly    C   23   
18           18    1    19               Shaq Lawson   DE   22   
19           19    1    20                Darron Lee  OLB   21   
20           20    1    21               Will Fuller   WR   22   
21           21    1    22              Josh Doctson   WR   23   
22           22    1    23          Laquon Treadwell   WR   21   
23           23    1    24       William Jackson III   CB   23   
24           24    1    25               Artie Burns   CB   21   
25           25    1    26              Paxton Lynch   QB   22   
26           26    1    27               Kenny Clark   DT   20   
27           27    1    28            Joshua Garnett    G   22   
28           28    1    29          Robert Nkemdiche   DT   21   
29           29    1    30             Vernon Butler   DT   22   
30           30    1    31             Germain Ifedi    G   22   
31           31  Rnd  Pick                    Player  Pos  Age   
32           32    2    32            Emmanuel Ogbah   DE   22   
33           33    2    33                Kevin Dodd   DE   24   
34           34    2    34              Jaylon Smith  OLB   21   
35           35    2    35              Hunter Henry   TE   21   
36           36    2    36                Myles Jack  OLB   21   
37           37    2    37               Chris Jones   DT   22   
38           38    2    38             Xavien Howard   CB   23   
39           39    2    39               Noah Spence   DE   22   
40           40    2    40          Sterling Shepard   WR   23   
41           41    2    41            Reggie Ragland  ILB   22   
42           42    2    42            Kamalei Correa   DE   22   
43           43    2    43            Austin Johnson   NT   22   
44           44    2    44                Jihad Ward   DE   22   
45           45    2    45             Derrick Henry   RB   22   
46           46    2    46          A'Shawn Robinson   DT   21   
47           47    2    47            Michael Thomas   WR   23   
48           48    2    48             Jason Spriggs    T   22   
49           49    2    49               Jarran Reed   DT   23   
50           50    2    50               Nick Martin    G   23   
51           51    2    51      Christian Hackenberg   QB   21   
52           52    2    52               Deion Jones  OLB   21   
53           53    2    53              Su'a Cravens  OLB   21   
54           54    2    54       Mackensie Alexander   CB   22   
55           55    2    55                Tyler Boyd   WR   21   
56           56    2    56            Cody Whitehair    G   24   
57           57    2    57                T.J. Green    S   21   
58           58    2    58                Sean Davis   CB   22   
59           59    2    59            Roberto 

In [44]:
# add 100 to the id so it has at least 3 numbers
draft['player_id'] = draft['player_id']+100
draft['player_id'] = draft['player_id']
draft

player_id  Rnd  Pick                    Player  Pos  Age  \
0           100    1     1                Jared Goff   QB   21   
1           101    1     2              Carson Wentz   QB   23   
2           102    1     3                 Joey Bosa   DE   21   
3           103    1     4           Ezekiel Elliott   RB   21   
4           104    1     5              Jalen Ramsey   CB   21   
5           105    1     6            Ronnie Stanley    T   22   
6           106    1     7          DeForest Buckner   DE   22   
7           107    1     8              Jack Conklin    T   22   
8           108    1     9             Leonard Floyd  OLB   23   
9           109    1    10                 Eli Apple   CB   21   
10          110    1    11     Vernon Hargreaves III   CB   21   
11          111    1    12           Sheldon Rankins   DT   22   
12          112    1    13             Laremy Tunsil    T   22   
13          113    1    14               Karl Joseph    S   22   
14          114    1    15             Corey Coleman   WR   22   
15          115    1    16             Taylor Decker    T   23   
16          116    1    17                Keanu Neal    S   21   
17          117    1    18                Ryan Kelly    C   23   
18          118    1    19               Shaq Lawson   DE   22   
19          119    1    20                Darron Lee  OLB   21   
20          120    1    21               Will Fuller   WR   22   
21          121    1    22              Josh Doctson   WR   23   
22          122    1    23          Laquon Treadwell   WR   21   
23          123    1    24       William Jackson III   CB   23   
24          124    1    25               Artie Burns   CB   21   
25          125    1    26              Paxton Lynch   QB   22   
26          126    1    27               Kenny Clark   DT   20   
27          127    1    28            Joshua Garnett    G   22   
28          128    1    29          Robert Nkemdiche   DT   21   
29          129    1    30             Vernon Butler   DT   22   
30          130    1    31             Germain Ifedi    G   22   
31          131  Rnd  Pick                    Player  Pos  Age   
32          132    2    32            Emmanuel Ogbah   DE   22   
33          133    2    33                Kevin Dodd   DE   24   
34          134    2    34              Jaylon Smith  OLB   21   
35          135    2    35              Hunter Henry   TE   21   
36          136    2    36                Myles Jack  OLB   21   
37          137    2    37               Chris Jones   DT   22   
38          138    2    38             Xavien Howard   CB   23   
39          139    2    39               Noah Spence   DE   22   
40          140    2    40          Sterling Shepard   WR   23   
41          141    2    41            Reggie Ragland  ILB   22   
42          142    2    42            Kamalei Correa   DE   22   
43          143    2    43            Austin Johnson   NT   22   
44          144    2    44                Jihad Ward   DE   22   
45          145    2    45             Derrick Henry   RB   22   
46          146    2    46          A'Shawn Robinson   DT   21   
47          147    2    47            Michael Thomas   WR   23   
48          148    2    48             Jason Spriggs    T   22   
49          149    2    49               Jarran Reed   DT   23   
50          150    2    50               Nick Martin    G   23   
51          151    2    51      Christian Hackenberg   QB   21   
52          152    2    52               Deion Jones  OLB   21   
53          153    2    53              Su'a Cravens  OLB   21   
54          154    2    54       Mackensie Alexander   CB   22   
55          155    2    55                Tyler Boyd   WR   21   
56          156    2    56            Cody Whitehair    G   24   
57          157    2    57                T.J. Green    S   21   
58          158    2    58                Sean Davis   CB   22   
59          159    2    59            Roberto 

In [8]:
pd.set_option('display.max_rows', None)

In [9]:
unique_colleges = draft.drop_duplicates(subset='college')
unique_colleges

player_id  Rnd  Pick                  Player  Pos  Age  \
0           100    1     1              Jared Goff   QB   21   
1           101    1     2            Carson Wentz   QB   23   
2           102    1     3               Joey Bosa   DE   21   
4           104    1     5            Jalen Ramsey   CB   21   
5           105    1     6          Ronnie Stanley    T   22   
6           106    1     7        DeForest Buckner   DE   22   
7           107    1     8            Jack Conklin    T   22   
8           108    1     9           Leonard Floyd  OLB   23   
10          110    1    11   Vernon Hargreaves III   CB   21   
11          111    1    12         Sheldon Rankins   DT   22   
12          112    1    13           Laremy Tunsil    T   22   
13          113    1    14             Karl Joseph    S   22   
14          114    1    15           Corey Coleman   WR   22   
17          117    1    18              Ryan Kelly    C   23   
18          118    1    19             Shaq Lawson   DE   22   
21          121    1    22            Josh Doctson   WR   23   
23          123    1    24     William Jackson III   CB   23   
24          124    1    25             Artie Burns   CB   21   
25          125    1    26            Paxton Lynch   QB   22   
26          126    1    27             Kenny Clark   DT   20   
27          127    1    28          Joshua Garnett    G   22   
29          129    1    30           Vernon Butler   DT   22   
30          130    1    31           Germain Ifedi    G   22   
31          131  Rnd  Pick                  Player  Pos  Age   
32          132    2    32          Emmanuel Ogbah   DE   22   
35          135    2    35            Hunter Henry   TE   21   
37          137    2    37             Chris Jones   DT   22   
39          139    2    39             Noah Spence   DE   22   
40          140    2    40        Sterling Shepard   WR   23   
42          142    2    42          Kamalei Correa   DE   22   
43          143    2    43          Austin Johnson   NT   22   
44          144    2    44              Jihad Ward   DE   22   
48          148    2    48           Jason Spriggs    T   22   
52          152    2    52             Deion Jones  OLB   21   
53          153    2    53            Su'a Cravens  OLB   21   
55          155    2    55              Tyler Boyd   WR   21   
56          156    2    56          Cody Whitehair    G   24   
58          158    2    58              Sean Davis   CB   22   
62          162    2    62         James Bradberry   CB   23   
63          163    2    63             Adam Gotsis   DT   23   
65          165    3    64             Kevin Byard    S   23   
68          168    3    67          Maliek Collins   DT   21   
71          171    3    70         Bronson Kaufusi   DE   25   
77          177    3    76            Shon Coleman    T   24   
79          179    3    78              Joe Thuney    G   23   
80          180    3    79           Isaac Seumalo    G   22   
83          183    3    82          Le'Raven Clark    T   23   
85          185    3    84          Kendall Fuller   CB   21   
87          187    3    86           Leonte Carroo   WR   22   
88          188    3    87              Nick Vigil  ILB   23   
90          190    3    89          Javon Hargrave   DT   23   
96          196    3    95          Graham Glasgow    C   24   
99          199    3    98          Justin Simmons    S   22   
101         201    4    99            Joe Schobert  OLB   22   
106         206    4   104             Tavon Young   CB   22   
107         207    4   105          Parker Ehinger    G   23   
108         208    4   106             Eric Murray   CB   22   
110         210    4   108              Ryan Smith   CB   23   
112         212    4   110            Tyler Higbee   TE   23   
113         213    4   111         Miles Killebrew    S   23   
118         218    4   116         Hassan Ridgeway   DT   21   
119         219    4   117           P

In [11]:
u_c = unique_colleges['college'].sort_values(axis=0, ascending=True)
u_c

1035                 Air Force
178                      Akron
17                     Alabama
495                Alabama St.
405          Albany State (GA)
145            Appalachian St.
223                    Arizona
164                Arizona St.
35                    Arkansas
304                    Ashland
77                      Auburn
71                         BYU
1192                  Ball St.
14                      Baylor
42                   Boise St.
99                 Boston Col.
992              Bowling Green
391                   Bucknell
515                    Buffalo
0                   California
231           Central Arkansas
350            Central Florida
216           Central Michigan
917            Charleston (WV)
325                  Charlotte
480                Chattanooga
107                 Cincinnati
18                     Clemson
466           Coastal Carolina
31                College/Univ
319                   Colorado
175               Colorado St.
315     

In [45]:
# North Dakota St.

draft.loc[draft['college'] == 'California', 'institution'] = 'University of California, Berkeley'
draft.loc[draft['college'] == 'North Dakota St.', 'institution'] = 'University of North Dakota'
draft.loc[draft['college'] == 'Ohio St.', 'institution'] = 'Ohio State University'
draft.loc[draft['college'] == 'Florida St.', 'institution'] = 'Florida State University'
draft.loc[draft['college'] == 'Notre Dame', 'institution'] = 'University of Notre Dame'
draft.loc[draft['college'] == 'Oregon', 'institution'] = 'University of Oregon'
draft.loc[draft['college'] == 'Michigan St.', 'institution'] = 'Michigan State University'
draft.loc[draft['college'] == 'Georgia', 'institution'] = 'University of Georgia'
draft.loc[draft['college'] == 'Florida', 'institution'] = 'Florida State University'
draft.loc[draft['college'] == 'Louisville', 'institution'] = 'University of Louisville '
draft.loc[draft['college'] == 'Mississippi', 'institution'] = 'University of Mississippi'
draft.loc[draft['college'] == 'West Virginia', 'institution'] = 'West Virginia University '
draft.loc[draft['college'] == 'Baylor', 'institution'] = 'Baylor University'
draft.loc[draft['college'] == 'Alabama', 'institution'] = 'University of Alabama at Birmingham '
draft.loc[draft['college'] == 'Clemson', 'institution'] = 'Clemson University'
draft.loc[draft['college'] == 'TCU', 'institution'] = 'Texas Christian University '
draft.loc[draft['college'] == 'Houston', 'institution'] = 'University of Houston'
draft.loc[draft['college'] == 'Miami (FL)', 'institution'] = 'University of Miami'
draft.loc[draft['college'] == 'Memphis', 'institution'] = 'University of Memphis'
draft.loc[draft['college'] == 'UCLA', 'institution'] = 'University of California, Los Angeles'
draft.loc[draft['college'] == 'Stanford', 'institution'] = 'Stanford University'
draft.loc[draft['college'] == 'Louisiana Tech', 'institution'] = 'Louisiana Tech University'
draft.loc[draft['college'] == 'Texas A&M', 'institution'] = 'Texas A & M University '
draft.loc[draft['college'] == 'Oklahoma St.', 'institution'] = 'Oklahoma State University '
draft.loc[draft['college'] == 'Arkansas', 'institution'] = 'University of Arkansas'
draft.loc[draft['college'] == 'Mississippi St.', 'institution'] = 'Mississippi State University '
draft.loc[draft['college'] == 'East. Kentucky', 'institution'] = 'Eastern Kentucky University'
draft.loc[draft['college'] == 'Oklahoma', 'institution'] = 'University of Oklahoma '
draft.loc[draft['college'] == 'Boise St.', 'institution'] = 'Boise State University'
draft.loc[draft['college'] == 'Penn St.', 'institution'] = 'Pennsylvania State University-Penn State Main Campus'
draft.loc[draft['college'] == 'Illinois', 'institution'] = 'University of Illinois at Urbana-Champaign'
draft.loc[draft['college'] == 'Indiana', 'institution'] = 'Indiana State University'
draft.loc[draft['college'] == 'LSU', 'institution'] = 'Louisiana State University - Baton Rouge'
draft.loc[draft['college'] == 'USC', 'institution'] = 'University of South Carolina'
draft.loc[draft['college'] == 'Pittsburgh', 'institution'] = 'University of Pittsburgh'
draft.loc[draft['college'] == 'Kansas St.', 'institution'] = 'Kansas State University'
draft.loc[draft['college'] == 'Maryland', 'institution'] = 'University of Maryland, College Park'
draft.loc[draft['college'] == 'Samford', 'institution'] = 'Samford University'
draft.loc[draft['college'] == 'Georgia Tech', 'institution'] = 'Georgia Institute of Technology'
draft.loc[draft['college'] == 'Middle Tenn. St.', 'institution'] = 'Middle Tennessee State University'
draft.loc[draft['college'] == 'Nebraska', 'institution'] = 'University of Nebraska - Lincoln'
draft.loc[draft['college'] == 'BYU', 'institution'] = 'Brigham Young University'
draft.loc[draft['college'] == 'Auburn', 'institution'] = 'Auburn University'
draft.loc[draft['college'] == 'North Carolina St.', 'institution'] = 'North Carolina State University - Raleigh'
draft.loc[draft['college'] == 'Oregon St.', 'institution'] = 'Oregon State University'
draft.loc[draft['college'] == 'Texas Tech', 'institution'] = 'Texas Tech University'
draft.loc[draft['college'] == 'Virginia Tech', 'institution'] = 'Virginia Polytechnic Institute and State University'
draft.loc[draft['college'] == 'Rutgers', 'institution'] = 'Rutgers University'
draft.loc[draft['college'] == 'Utah St.', 'institution'] = 'Utah State University'
draft.loc[draft['college'] == 'South Carolina St.', 'institution'] = 'South Carolina State University'
draft.loc[draft['college'] == 'Michigan', 'institution'] = 'University of Michigan-Ann Arbor'
draft.loc[draft['college'] == 'Boston Col.', 'institution'] = 'Boston College'
draft.loc[draft['college'] == ' Wisconsin', 'institution'] = 'University of Wisconsin - Madison'
draft.loc[draft['college'] == 'Temple', 'institution'] = 'Temple University'
draft.loc[draft['college'] == 'Cincinnati', 'institution'] = 'University of Cincinnati'
draft.loc[draft['college'] == ' Minnesota', 'institution'] = 'University of Minnesota, Twin Cities'
draft.loc[draft['college'] == 'North Carolina Central', 'institution'] = 'North Carolina Central University'
draft.loc[draft['college'] == 'Western Kentucky', 'institution'] = 'Western Kentucky University'
draft.loc[draft['college'] == 'Southern Utah', 'institution'] = 'Southern Utah University'
draft.loc[draft['college'] == 'Texas', 'institution'] = 'The University of Texas at Austin'
draft.loc[draft['college'] == 'South Carolina', 'institution'] = 'University of South Carolina'
draft.loc[draft['college'] == 'San Jose St.', 'institution'] = 'San Jose State University'
draft.loc[draft['college'] == 'Manitoba', 'institution'] = 'University of Manitoba'
draft.loc[draft['college'] == 'Western Michigan', 'institution'] = 'Western Michigan University'
draft.loc[draft['college'] == 'Northern Iowa', 'institution'] = 'University of Northern Iowa'
draft.loc[draft['college'] == 'Missouri', 'institution'] = 'University of Missouri'
draft.loc[draft['college'] == 'Utah', 'institution'] = 'University of Utah'
draft.loc[draft['college'] == 'Northwestern', 'institution'] = 'Northwestern State University of Louisiana'
draft.loc[draft['college'] == 'Princeton', 'institution'] = 'Princeton University'
draft.loc[draft['college'] == 'Massachusetts', 'institution'] = 'University of Massachusetts Amherst'
draft.loc[draft['college'] == 'Prairie View A&M', 'institution'] = 'Prairie View A & M University'
draft.loc[draft['college'] == 'Western Michigan', 'institution'] = 'Western Michigan University '
draft.loc[draft['college'] == 'Northern Iowa', 'institution'] = 'University of Northern Iowa'
draft.loc[draft['college'] == 'West Alabama', 'institution'] = 'University of West Alabama'
draft.loc[draft['college'] == 'Arizona St.', 'institution'] = 'Arizona State University'
draft.loc[draft['college'] == 'Washington St.', 'institution'] = 'Washington State University'
draft.loc[draft['college'] == 'Grand Valley St.', 'institution'] = 'Grand Valley State University'
draft.loc[draft['college'] == 'Appalachian St.', 'institution'] = 'Appalachian State University'

draft.loc[draft['college'] == 'Midwestern St.', 'institution'] = 'Midwestern State University'
draft.loc[draft['college'] == 'Harvard', 'institution'] = 'Harvard University'
draft.loc[draft['college'] == 'Colorado St.', 'institution'] = 'Colorado State University'
draft.loc[draft['college'] == 'Georgia Southern', 'institution'] = 'Georgia Southern University'
draft.loc[draft['college'] == 'La-Monroe', 'institution'] = 'University of Louisiana Monroe'
draft.loc[draft['college'] == 'Akron', 'institution'] = 'The University of Akron'
draft.loc[draft['college'] == 'Montana', 'institution'] = 'The University of Montana'
draft.loc[draft['college'] == 'William & Mary', 'institution'] = 'College of William and Mary'
draft.loc[draft['college'] == 'Texas-San Antonio', 'institution'] = 'The University of Texas at San Antonio'
draft.loc[draft['college'] == 'Purdue', 'institution'] = 'Purdue University - West Lafayette'
draft.loc[draft['college'] == 'Kentucky', 'institution'] = 'University of Kentucky'
draft.loc[draft['college'] == 'Southeastern Louisiana', 'institution'] = 'Southeastern Louisiana University'
draft.loc[draft['college'] == 'Southern Miss', 'institution'] = 'University of Southern Mississippi'
draft.loc[draft['college'] == 'Eastern Illinois', 'institution'] = 'Eastern Illinois University'
draft.loc[draft['college'] == 'Virginia', 'institution'] = 'University of Virginia'
draft.loc[draft['college'] == 'Central Michigan', 'institution'] = 'Central Michigan University'
draft.loc[draft['college'] == 'East. Michigan', 'institution'] = 'Eastern Michigan University'
draft.loc[draft['college'] == 'Arizona', 'institution'] = 'University of Arizona'
draft.loc[draft['college'] == 'Washington', 'institution'] = 'University of Washington'
draft.loc[draft['college'] == 'Central Arkansas', 'institution'] = 'University of Central Arkansas'
draft.loc[draft['college'] == 'Vanderbilt', 'institution'] = 'Vanderbilt University'
draft.loc[draft['college'] == 'Syracuse', 'institution'] = 'Syracuse University'
draft.loc[draft['college'] == 'Sam Houston St.', 'institution'] = 'Sam Houston State University'
draft.loc[draft['college'] == 'Maine', 'institution'] = 'University of Maine'
draft.loc[draft['college'] == 'Iowa', 'institution'] = 'University of Iowa'
draft.loc[draft['college'] == 'Montana St.', 'institution'] = 'Montana State University'
draft.loc[draft['college'] == 'North Carolina', 'institution'] = 'University of North Carolina at Greensboro'
draft.loc[draft['college'] == 'Tennessee', 'institution'] = 'University of Tennessee'
draft.loc[draft['college'] == 'East Carolina', 'institution'] = 'East Carolina University'
draft.loc[draft['college'] == 'South Alabama', 'institution'] = 'University of South Alabama'
draft.loc[draft['college'] == 'Ashland', 'institution'] = 'Ashland University'
draft.loc[draft['college'] == 'Connecticut', 'institution'] = 'Central Connecticut State University'
draft.loc[draft['college'] == 'Villanova', 'institution'] = 'Villanova University'
draft.loc[draft['college'] == 'Colorado', 'institution'] = 'University of Colorado Boulder'
draft.loc[draft['college'] == 'Charlotte', 'institution'] = 'University of North Carolina at Charlotte'
draft.loc[draft['college'] == 'East. Washington', 'institution'] = 'Eastern Washington University'
draft.loc[draft['college'] == 'Ohio', 'institution'] = 'Ohio University'
draft.loc[draft['college'] == 'Youngstown St.', 'institution'] = 'Youngstown State University'
draft.loc[draft['college'] == ' Troy', 'institution'] = 'Troy University'
draft.loc[draft['college'] == 'Toledo', 'institution'] = 'University of Toledo'
draft.loc[draft['college'] == 'Louisiana', 'institution'] = 'University of Louisiana at Lafayette'
draft.loc[draft['college'] == 'Central Florida', 'institution'] = 'University of Central Florida'
draft.loc[draft['college'] == 'Northern Illinois', 'institution'] = 'Northern Illinois University'
draft.loc[draft['college'] == 'Grambling St.', 'institution'] = 'Grambling State University'
draft.loc[draft['college'] == 'Florida International', 'institution'] = 'Florida International University'
draft.loc[draft['college'] == 'Lamar', 'institution'] = 'Lamar University'
draft.loc[draft['college'] == 'Florida Atlantic', 'institution'] = 'Florida Atlantic University'
draft.loc[draft['college'] == 'North Carolina A&T', 'institution'] = 'North Carolina A & T State University'
draft.loc[draft['college'] == 'San Diego St.', 'institution'] = 'San Diego State University'
draft.loc[draft['college'] == 'Bucknell', 'institution'] = 'Bucknell University'
draft.loc[draft['college'] == 'South Florida', 'institution'] = 'University of South Florida'
draft.loc[draft['college'] == 'Albany State (GA)', 'institution'] = 'Albany State University'
draft.loc[draft['college'] == 'Kutztown (PA)', 'institution'] = 'Kutztown University of Pennsylvania'
draft.loc[draft['college'] == 'Wyoming', 'institution'] = 'University of Wyoming'
draft.loc[draft['college'] == 'San Diego', 'institution'] = 'University of San Diego'
draft.loc[draft['college'] == 'Wake Forest', 'institution'] = 'Wake Forest University'
draft.loc[draft['college'] == 'Drake', 'institution'] = 'Drake University'
draft.loc[draft['college'] == 'West Georgia', 'institution'] = 'University of West Georgia'
draft.loc[draft['college'] == 'Tulane', 'institution'] = 'Tulane University'
draft.loc[draft['college'] == 'Coastal Carolina', 'institution'] = 'Coastal Carolina University'
draft.loc[draft['college'] == 'Georgia St.', 'institution'] = 'Georgia State University'
draft.loc[draft['college'] == 'Chattanooga', 'institution'] = 'The University of Tennessee at Chattanooga'
draft.loc[draft['college'] == 'East Central (OK)', 'institution'] = 'East Central University'




draft.loc[draft['college'] == 'Texas-El Paso', 'institution'] = 'University of Texas at El Paso'
draft.loc[draft['college'] == 'Tennessee St.', 'institution'] = 'Tennessee State University'
draft.loc[draft['college'] == 'Miami (OH)', 'institution'] = 'Miami University-Oxford'


In [46]:
draft.loc[draft['college'] == 'Alabama St.', 'institution'] = 'Alabama State University'
draft.loc[draft['college'] == 'Buffalo', 'institution'] = 'University at Buffalo'
draft.loc[draft['college'] == ' Nevada', 'institution'] = 'University of Nevada-Reno'
draft.loc[draft['college'] == 'SMU', 'institution'] = 'Southern Methodist University'
draft.loc[draft['college'] == 'South Dakota St.', 'institution'] = 'South Dakota State University'
draft.loc[draft['college'] == 'Fort Hays St.', 'institution'] = 'Fort Hays State University'
draft.loc[draft['college'] == 'Humboldt St.', 'institution'] = 'Humboldt State University'
draft.loc[draft['college'] == 'Richmond', 'institution'] = 'University of Richmond'

draft.loc[draft['college'] == 'S.F. Austin', 'institution'] = 'Stephen F Austin State University'
draft.loc[draft['college'] == 'Kansas', 'institution'] = 'University of Kansas'
draft.loc[draft['college'] == 'Weber St.', 'institution'] = 'Weber State University'
draft.loc[draft['college'] == 'New Mexico St.', 'institution'] = 'New Mexico State University'
draft.loc[draft['college'] == 'Fordham', 'institution'] = 'Fordham University'
draft.loc[draft['college'] == 'Pennsylvania', 'institution'] = 'University of Pennsylvania'
draft.loc[draft['college'] == 'Delaware', 'institution'] = 'University of Delaware'
draft.loc[draft['college'] == ' Illinois St.', 'institution'] = 'Illinois State University'
draft.loc[draft['college'] == 'Jacksonville St.', 'institution'] = 'Jacksonville State University'
draft.loc[draft['college'] == 'Yale', 'institution'] = 'Yale University'
draft.loc[draft['college'] == 'Virginia St.', 'institution'] = 'Virginia State University'
draft.loc[draft['college'] == 'Wagner', 'institution'] = 'Wagner College'
draft.loc[draft['college'] == 'New Mexico', 'institution'] = 'The University of New Mexico - Albuquerque'
draft.loc[draft['college'] == 'Ferris St.', 'institution'] = 'Ferris State University'
draft.loc[draft['college'] == 'Western Carolina', 'institution'] = 'Western Carolina University'
draft.loc[draft['college'] == 'SE Missouri St.', 'institution'] = 'Southeast Missouri State University'

draft.loc[draft['college'] == 'Duke', 'institution'] = 'Duke University'
draft.loc[draft['college'] == 'Hawaii', 'institution'] = 'University of Hawaii at Manoa'
draft.loc[draft['college'] == 'Iowa St.', 'institution'] = 'Iowa State University'
draft.loc[draft['college'] == 'Western Illinois', 'institution'] = 'Western Illinois University'
draft.loc[draft['college'] == 'Sioux Falls', 'institution'] = 'University of Sioux Falls'
draft.loc[draft['college'] == 'Old Dominion', 'institution'] = 'Old Dominion University'
draft.loc[draft['college'] == 'Murray St.', 'institution'] = 'Murray State University'
draft.loc[draft['college'] == 'Charleston (WV)', 'institution'] = 'University of Charleston'
draft.loc[draft['college'] == 'Tarleton St.', 'institution'] = 'Tarleton State University'
draft.loc[draft['college'] == 'Southern Illinois', 'institution'] = 'Southern Illinois University Carbondale'
draft.loc[draft['college'] == 'Fresno St.', 'institution'] = 'California State University-Fresno'
draft.loc[draft['college'] == 'Washburn', 'institution'] = 'Washburn University'
draft.loc[draft['college'] == 'Elon', 'institution'] = 'Elon University'
draft.loc[draft['college'] == 'Bowling Green', 'institution'] = 'Bowling Green State University'
draft.loc[draft['college'] == 'James Madison', 'institution'] = 'James Madison University'
draft.loc[draft['college'] == 'Valdosta St.', 'institution'] = 'Valdosta State University'
draft.loc[draft['college'] == 'Idaho', 'institution'] = 'University of Idaho'
draft.loc[draft['college'] == 'Morgan St.', 'institution'] = 'Morgan State University'
draft.loc[draft['college'] == 'Air Force', 'institution'] = 'United States Air Force Academy'
draft.loc[draft['college'] == 'Lenoir-Rhyne', 'institution'] = 'Lenoir-Rhyne University'
draft.loc[draft['college'] == 'Dayton', 'institution'] = 'University of Dayton'
draft.loc[draft['college'] == "Saint John's (MN)", 'institution'] = "Saint John's University in Collegeville"
draft.loc[draft['college'] == 'Tulsa', 'institution'] = 'University of Tulsa'


draft.loc[draft['college'] == 'Liberty', 'institution'] = 'Liberty University'
draft.loc[draft['college'] == 'Ball St.', 'institution'] = 'Ball State University'
draft.loc[draft['college'] == 'Marshall', 'institution'] = 'Marshall University'
draft.loc[draft['college'] == 'Rhode Island', 'institution'] = 'University of Rhode Island'


draft.loc[draft['college'] == 'Wisconsin', 'institution'] = 'University of Wisconsin - Madison'
draft.loc[draft['college'] == 'Minnesota', 'institution'] = 'University of Minnesota, Twin Cities'
draft.loc[draft['college'] == 'Troy', 'institution'] = 'Troy University'
draft.loc[draft['college'] == 'Nevada', 'institution'] = 'University of Nevada-Reno'

draft.loc[draft['college'] == 'Navy', 'institution'] = 'Navy'
draft.loc[draft['college'] == 'Louisville', 'institution'] = 'University of Louisville'

draft.loc[draft['college'] == 'West Virginia', 'institution'] = 'West Virginia University'
draft.loc[draft['college'] == 'Louisville', 'institution'] = 'University of Louisville'
draft.loc[draft['college'] == 'Alabama', 'institution'] = 'The University of Alabama'
draft.loc[draft['college'] == 'TCU', 'institution'] = 'Texas Christian University'
draft.loc[draft['college'] == 'Texas A&M', 'institution'] = 'Texas A&M University'
draft.loc[draft['college'] == 'Oklahoma St.', 'institution'] = 'Oklahoma State University'
draft.loc[draft['college'] == 'Mississippi St.', 'institution'] = 'Mississippi State University'

draft.loc[draft['college'] == 'East. Kentucky', 'institution'] = 'Eastern Kentucky University'
draft.loc[draft['college'] == 'Oklahoma', 'institution'] = 'University of Oklahoma'
draft.loc[draft['college'] == 'Penn St.', 'institution'] = 'Pennsylvania State University'

In [47]:

print(len(draft))
draft = draft.dropna()
draft

1301


player_id Rnd Pick                    Player  Pos Age  \
0           100   1    1                Jared Goff   QB  21   
1           101   1    2              Carson Wentz   QB  23   
2           102   1    3                 Joey Bosa   DE  21   
3           103   1    4           Ezekiel Elliott   RB  21   
4           104   1    5              Jalen Ramsey   CB  21   
5           105   1    6            Ronnie Stanley    T  22   
6           106   1    7          DeForest Buckner   DE  22   
7           107   1    8              Jack Conklin    T  22   
8           108   1    9             Leonard Floyd  OLB  23   
9           109   1   10                 Eli Apple   CB  21   
10          110   1   11     Vernon Hargreaves III   CB  21   
11          111   1   12           Sheldon Rankins   DT  22   
12          112   1   13             Laremy Tunsil    T  22   
13          113   1   14               Karl Joseph    S  22   
14          114   1   15             Corey Coleman   WR  22   
15          115   1   16             Taylor Decker    T  23   
16          116   1   17                Keanu Neal    S  21   
17          117   1   18                Ryan Kelly    C  23   
18          118   1   19               Shaq Lawson   DE  22   
19          119   1   20                Darron Lee  OLB  21   
20          120   1   21               Will Fuller   WR  22   
21          121   1   22              Josh Doctson   WR  23   
22          122   1   23          Laquon Treadwell   WR  21   
23          123   1   24       William Jackson III   CB  23   
24          124   1   25               Artie Burns   CB  21   
25          125   1   26              Paxton Lynch   QB  22   
26          126   1   27               Kenny Clark   DT  20   
27          127   1   28            Joshua Garnett    G  22   
28          128   1   29          Robert Nkemdiche   DT  21   
29          129   1   30             Vernon Butler   DT  22   
30          130   1   31             Germain Ifedi    G  22   
32          132   2   32            Emmanuel Ogbah   DE  22   
33          133   2   33                Kevin Dodd   DE  24   
34          134   2   34              Jaylon Smith  OLB  21   
35          135   2   35              Hunter Henry   TE  21   
36          136   2   36                Myles Jack  OLB  21   
37          137   2   37               Chris Jones   DT  22   
38          138   2   38             Xavien Howard   CB  23   
39          139   2   39               Noah Spence   DE  22   
40          140   2   40          Sterling Shepard   WR  23   
41          141   2   41            Reggie Ragland  ILB  22   
42          142   2   42            Kamalei Correa   DE  22   
43          143   2   43            Austin Johnson   NT  22   
44          144   2   44                Jihad Ward   DE  22   
45          145   2   45             Derrick Henry   RB  22   
46          146   2   46          A'Shawn Robinson   DT  21   
47          147   2   47            Michael Thomas   WR  23   
48          148   2   48             Jason Spriggs    T  22   
49          149   2   49               Jarran Reed   DT  23   
50          150   2   50               Nick Martin    G  23   
51          151   2   51      Christian Hackenberg   QB  21   
52          152   2   52               Deion Jones  OLB  21   
53          153   2   53              Su'a Cravens  OLB  21   
54          154   2   54       Mackensie Alexander   CB  22   
55          155   2   55                Tyler Boyd   WR  21   
56          156   2   56            Cody Whitehair    G  24   
57          157   2   57                T.J. Green    S  21   
58          158   2   58                Sean Davis   CB  22   
59          159   2   59            Roberto Aguayo    K  22   
60          160   2   60               Cyrus Jones   CB  22   
61          161   2   61                 Vonn Bell    S  21   
62          162   2   62           James Bradberry   CB  23   
63          163   2   63             

In [48]:
print(len(draft))

1267


In [52]:
col = pd.read_csv('../resources/teams_conf.csv')
col

i_id                                        Institution  \
0     1228                                  Baylor University   
1     5388                              Iowa State University   
2     5655                            Kansas State University   
3     8002                          Oklahoma State University   
4    10559                         Texas Christian University   
5    10578                              Texas Tech University   
6    11369                               University of Kansas   
7    11514                             University of Oklahoma   
8    10802                  The University of Texas at Austin   
9    12284                           West Virginia University   
10   11313                              University of Florida   
11   11320                              University of Georgia   
12   11374                             University of Kentucky   
13   11453                             University of Missouri   
14   11674                       University of South Carolina   
15   11713                            University of Tennessee   
16   11915                              Vanderbilt University   
17   10771                          The University of Alabama   
18   11186                             University of Arkansas   
19     893                                  Auburn University   
20    6245           Louisiana State University - Baton Rouge   
21   11450                          University of Mississippi   
22    7049                       Mississippi State University   
23   10551                               Texas A&M University   
24   11257                      University of Central Florida   
25   11265                           University of Cincinnati   
26    3416                           East Carolina University   
27   11347                              University of Houston   
28   11435                              University of Memphis   
29   11684                        University of South Florida   
30    9934                      Southern Methodist University   
31   10498                                  Temple University   
32   10986                                  Tulane University   
33   11728                                University of Tulsa   
34   12374                           Wichita State University   
35    1430                                     Boston College   
36    2527                                 Clemson University   
37    4033                           Florida State University   
38   11404                           University of Louisville   
39    7692          North Carolina State University - Raleigh   
40   11511                           University of Notre Dame   
41   10253                                Syracuse University   
42   12163                             Wake Forest University   
43    3292                                    Duke University   
44    4277                    Georgia Institute of Technology   
45   11437                                University of Miami   
46   11495        University of North Carolina at Chapel Hill   
47   11615                           University of Pittsburgh   
48   11746                             University of Virginia   
49   12006  Virginia Polytechnic Institute and State Unive...   
50    5216                     Indiana University Bloomington   
51   11423               University of Maryland, College Park   
52   11438                   University of Michigan-Ann Arbor   
53    6916                          Michigan State University   
54    7977                              Ohio State University   
55    8420                      Pennsylvania State University   
56    9080                                 Rutgers University   
57   11357         University of Illinois at Urbana-Champaign   
58   11362                                 University of Iowa   
59   11445               University of Minnesota, Twin Cities   
60   11472                   University o

In [53]:
draft1 = draft.merge(col, left_on='institution', right_on='Institution', how='inner')
draft1.sort_values('i_id')


player_id Rnd Pick                    Player  Pos Age  \
1200        902   1   23              Tytus Howard    T  23   
1199        595   7  231                Jylan Ware    T  23   
944         245   5  142              Ronald Blair   DE  23   
945         835   6  213             Colby Gossett    G  23   
946        1234   3   93           Darrynton Evans   RB  22   
947        1249   4  107       Akeem Davis-Gaither   LB  22   
956         264   5  161       Christian Westerman    G  23   
957         330   7  225              Devin Lucien   WR  23   
958         588   7  224             Zane Gonzalez    K  22   
959         751   4  131             Kalen Ballage   RB  22   
960         800   6  178             Christian Sam  ILB  22   
961         805   6  183                 Sam Jones    G  22   
962         911   1   32              N'Keal Harry   WR  21   
964        1164   1   25             Brandon Aiyuk   WR  22   
965        1367   7  222              Eno Benjamin   RB  21   
963        1007   4  125               Renell Wren   DT  23   
715        1054   5  171            Darius Slayton   WR  22   
723        1300   5  157             Daniel Thomas    S  22   
722        1287   4  145             Jack Driscoll    G  23   
721        1187   2   47           Marlon Davidson   DE  22   
720        1169   1   30          Noah Igbinoghene   CB  20   
719        1146   1    7             Derrick Brown   DT  22   
718        1120   7  235         Dontavius Russell   DT  23   
717        1118   7  233              Chandler Cox   RB  23   
716        1094   6  210             Deshaun Davis   LB  23   
714        1015   4  133           Jarrett Stidham   QB  23   
713         975   3   94                Jamel Dean   CB  22   
712         788   5  167            Daniel Carlson    K  23   
724        1354   6  210       Prince Tega Wanogho    T  22   
711         681   2   63             Carlton Davis   CB  21   
709         655   2   37              Braden Smith    G  22   
708         599   7  235             Joshua Holsey   DB  23   
707         571   6  208                 Rudy Ford    S  22   
706         477   4  116               Carl Lawson  OLB  22   
705         453   3   93          Montravius Adams   DT  22   
704         300   6  196            Blake Countess   CB  23   
703         216   4  114             Ricardo Louis   WR  22   
702         177   3   76              Shon Coleman    T  24   
710         661   2   43           Kerryon Johnson   RB  21   
1251       1292   5  149              Danny Pinter    G  24   
231         607   7  243               Kyle Fuller    C  23   
232         948   3   67                Jalen Hurd   WR  23   
233        1199   2   59               Denzel Mims   WR  22   
230         321   6  217              Rico Gathers   TE  22   
228         271   5  168            Spencer Drango    G  23   
227         224   4  122           Andrew Billings   NT  21   
234        1272   4  130               James Lynch   DT  21   
226         138   2   38             Xavien Howard   CB  23   
225         114   1   15             Corey Coleman   WR  22   
229         314   6  210              Jimmy Landes   LS  24   
235        1328   6  184              Bravvion Roy   DT  23   
236        1379   7  234             Clay Johnston   LB  24   
519         198   3   97             Rees Odhiambo    G  23   
527        1311   5  168            John Hightower   WR  24   
526        1307   5  164             Curtis Weaver   DE  22   
525        1198   2   58            Ezra Cleveland    T  22   
524         983   3  102        Alexander Mattison   RB  21   
523         830   6  208        Cedrick Wilson Jr.   WR  22   
522         636   1   19      Leighton Vander Esch  OLB  22   
521         558   6  195            Tanner Vallejo   LB  22   
520         524   5  162          Jeremy McNichols   RB  21   
518         172   3   71           Darian Thompson    S  22   
517         142   2   42            K

In [54]:
player_df = draft1[['player_id', 'Player', 'i_id']]
nfl_draft = draft1[['player_id','Pick','Rnd','year']]


In [55]:
# save to csv


# draft.to_csv('../resources/nfl_draft_id', index=False)

In [56]:
# save to csv

player_df.to_csv('../resources/nfl_player_table.csv', index=False)
nfl_draft.to_csv('../resources/nfl_draft_table.csv', index=False)

In [57]:
con = pd.read_csv('../resources/teams_conf.csv')

In [58]:
con

i_id                                        Institution  \
0     1228                                  Baylor University   
1     5388                              Iowa State University   
2     5655                            Kansas State University   
3     8002                          Oklahoma State University   
4    10559                         Texas Christian University   
5    10578                              Texas Tech University   
6    11369                               University of Kansas   
7    11514                             University of Oklahoma   
8    10802                  The University of Texas at Austin   
9    12284                           West Virginia University   
10   11313                              University of Florida   
11   11320                              University of Georgia   
12   11374                             University of Kentucky   
13   11453                             University of Missouri   
14   11674                       University of South Carolina   
15   11713                            University of Tennessee   
16   11915                              Vanderbilt University   
17   10771                          The University of Alabama   
18   11186                             University of Arkansas   
19     893                                  Auburn University   
20    6245           Louisiana State University - Baton Rouge   
21   11450                          University of Mississippi   
22    7049                       Mississippi State University   
23   10551                               Texas A&M University   
24   11257                      University of Central Florida   
25   11265                           University of Cincinnati   
26    3416                           East Carolina University   
27   11347                              University of Houston   
28   11435                              University of Memphis   
29   11684                        University of South Florida   
30    9934                      Southern Methodist University   
31   10498                                  Temple University   
32   10986                                  Tulane University   
33   11728                                University of Tulsa   
34   12374                           Wichita State University   
35    1430                                     Boston College   
36    2527                                 Clemson University   
37    4033                           Florida State University   
38   11404                           University of Louisville   
39    7692          North Carolina State University - Raleigh   
40   11511                           University of Notre Dame   
41   10253                                Syracuse University   
42   12163                             Wake Forest University   
43    3292                                    Duke University   
44    4277                    Georgia Institute of Technology   
45   11437                                University of Miami   
46   11495        University of North Carolina at Chapel Hill   
47   11615                           University of Pittsburgh   
48   11746                             University of Virginia   
49   12006  Virginia Polytechnic Institute and State Unive...   
50    5216                     Indiana University Bloomington   
51   11423               University of Maryland, College Park   
52   11438                   University of Michigan-Ann Arbor   
53    6916                          Michigan State University   
54    7977                              Ohio State University   
55    8420                      Pennsylvania State University   
56    9080                                 Rutgers University   
57   11357         University of Illinois at Urbana-Champaign   
58   11362                                 University of Iowa   
59   11445               University of Minnesota, Twin Cities   
60   11472                   University o

In [59]:
conf = con[['c_id', 'Conference']]
conf = conf.drop_duplicates()
conf

c_id            Conference
0     6784                Big 12
10    8588                   SEC
24    5440                   AAC
35    2061                   ACC
50    7907               Big Ten
64    2946                 C-USA
78    6845                   MAC
90    8019                    MW
101   4065                PAC-12
113   6493                   SBC
125   1825                  MVFC
136   1410    Big Sky Conference
147   2489  Big South Conference
159   8725                   CAA
169  10209            Ivy League
177   5741                  MEAC
185   3381                   NEC
196   1493                   OVC
202   5961        Patriot League
212   4593                   PFL
223   3853                 SoCon
233   8827                   SLC
241   1593                  SWAC
253   7676                   WAC
268   5923           Independent
269      1               Foreign
272   3948                DIV-II
276   5497                  ASUN
289   6358               DIV-III

In [ ]:
conf.to_csv('../resources/ncaa_conferences_table.csv', index=False)

In [60]:
team = con[['i_id', 'c_id', 'Institution']]
team

i_id   c_id                                        Institution
0     1228   6784                                  Baylor University
1     5388   6784                              Iowa State University
2     5655   6784                            Kansas State University
3     8002   6784                          Oklahoma State University
4    10559   6784                         Texas Christian University
5    10578   6784                              Texas Tech University
6    11369   6784                               University of Kansas
7    11514   6784                             University of Oklahoma
8    10802   6784                  The University of Texas at Austin
9    12284   6784                           West Virginia University
10   11313   8588                              University of Florida
11   11320   8588                              University of Georgia
12   11374   8588                             University of Kentucky
13   11453   8588                             University of Missouri
14   11674   8588                       University of South Carolina
15   11713   8588                            University of Tennessee
16   11915   8588                              Vanderbilt University
17   10771   8588                          The University of Alabama
18   11186   8588                             University of Arkansas
19     893   8588                                  Auburn University
20    6245   8588           Louisiana State University - Baton Rouge
21   11450   8588                          University of Mississippi
22    7049   8588                       Mississippi State University
23   10551   8588                               Texas A&M University
24   11257   5440                      University of Central Florida
25   11265   5440                           University of Cincinnati
26    3416   5440                           East Carolina University
27   11347   5440                              University of Houston
28   11435   5440                              University of Memphis
29   11684   5440                        University of South Florida
30    9934   5440                      Southern Methodist University
31   10498   5440                                  Temple University
32   10986   5440                                  Tulane University
33   11728   5440                                University of Tulsa
34   12374   5440                           Wichita State University
35    1430   2061                                     Boston College
36    2527   2061                                 Clemson University
37    4033   2061                           Florida State University
38   11404   2061                           University of Louisville
39    7692   2061          North Carolina State University - Raleigh
40   11511   2061                           University of Notre Dame
41   10253   2061                                Syracuse University
42   12163   2061                             Wake Forest University
43    3292   2061                                    Duke University
44    4277   2061                    Georgia Institute of Technology
45   11437   2061                                University of Miami
46   11495   2061        University of North Carolina at Chapel Hill
47   11615   2061                           University of Pittsburgh
48   11746   2061                             University of Virginia
49   12006   2061  Virginia Polytechnic Institute and State Unive...
50    5216   7907                     Indiana University Bloomington
51   11423   7907               University of Maryland, College Park
52   11438   7907                   University of Michigan-Ann Arbor
53    6916   7907                          Michigan State University
54    7977   7907                              Ohio State University
55    8420   7907                      Pennsylvania State University
56    9080   7907                                 Rutgers University
57  

In [61]:
team.to_csv('../resources/ncaa_teams_table.csv',index=False)

In [ ]:
a = pd.read_html('https://www.ucribs.com/blog-post/ncaa-football-teams-made-more-money-than-many-nfl-teams-in-2015-infographic/')
a

In [ ]:
revenue = a[0]
revenue

In [ ]:
team10 = team.merge(revenue, right_on= 'Team', left_on = 'Institution', how='outer')
team10['year'] = 2015
team10

In [ ]:
teams_table = team10[['i_id', 'c_id', 'Team']]
teams_table

In [ ]:
team